# Introduction
State notebook purpose here

### Imports
Import libraries and write settings here.

In [1]:
# Data manipulation
import pandas as pd
import numpy as np
from sklearn.datasets import load_svmlight_file

# Options for pandas
pd.options.display.max_columns = 50
pd.options.display.max_rows = 30

# Display all cell outputs
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'last_expr'
from IPython.display import clear_output
from IPython import get_ipython
ipython = get_ipython()

# autoreload extension
if 'autoreload' not in ipython.extension_manager.loaded:
    %load_ext autoreload

%autoreload 2

# Visualizations
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode(connected=True)
import xgboost as xgb
from scipy.special import expit
from collections import defaultdict
from sklearn.tree import DecisionTreeRegressor
from numba import jit
from multiprocessing import Pool
from catboost import CatBoost, Pool, MetricVisualizer
from copy import deepcopy
from scipy import sparse
import copy
from sklearn.preprocessing import PolynomialFeatures

In [2]:
file = open("check/train.marks.tsv/train.marks.tsv", 'r')
train=[]
for l in file.readlines():
    splits=l.split('\t')
    train.append([int(splits[0]),int(splits[1]), int(splits[2])])
#train=np.array(train)
file.close()

In [3]:
file = open("check/sample.csv/sample.csv", 'r')
test=[]
for l in file.readlines():
    splits=l.split(',')
    test.append([int(splits[0]),int(splits[1])])
file.close()

In [4]:
file = open("check/queries.tsv", 'r')
QUERY={}
for l in file.readlines():
    splits=l.split('\t')
    QUERY[int(splits[0])]=splits[1]
file.close()

In [6]:
Data = {}
for i in range(11):
    file = open("QDocs/CTR/OnlyDocs/part-r-000"+str(i).zfill(2),'r')
    for l in file.readlines():
        d=[]
        splits=l.split('\t')
        d.append(float(splits[1]))
        d.append(float(splits[2]))
        d.append(float(splits[3]))
        d.append(float(splits[4]))
        d.append(float(splits[5]))
        d.append(float(splits[6]))
        d.append(float(splits[7]))
        d.append(float(splits[8]))
        d.append(float(splits[9]))
        d.append(float(splits[10]))
        d.append(float(splits[11]))
        d.append(float(splits[12]))
        Data[int(splits[0])]=np.array(d)
    file.close()

In [10]:
Data_PBM = {}
for i in range(11):
    file = open("New_Data/PBM/part-r-000"+str(i).zfill(2),'r')
    for l in file.readlines():
        d=[]
        splits=l.split('\t')
        d.append(float(splits[2]))
        d.append(float(splits[3]))
        d.append(float(splits[4]))
        d.append(float(splits[5]))
        d.append(float(splits[6]))
        d.append(float(splits[7]))
        d.append(float(splits[8]))
        d.append(float(splits[9]))
        d.append(float(splits[10]))
        d.append(float(splits[11]))
        d.append(float(splits[12]))
        d.append(float(splits[13]))
        d.append(float(splits[14]))
        d.append(float(splits[15]))
        d.append(float(splits[16]))
        Data_PBM[splits[0]+"|"+splits[1]]=np.array(d)
    file.close()

In [21]:
Data_sDBN = {}
for i in range(11):
    file = open("New_Data/sDBN/part-r-000"+str(i).zfill(2),'r')
    for l in file.readlines():
        d=[]
        splits=l.split('\t')
        d.append(float(splits[2]))
        d.append(float(splits[3]))
        d.append(float(splits[4]))
        Data_sDBN[splits[0]+"|"+splits[1]]=np.array(d)
    file.close()

In [68]:
file = open("CTR/part-r-00000",'r')
Data = {}
for l in file.readlines():
    d=[]
    splits=l.split('\t')
    d.append(float(splits[1]))
    d.append(float(splits[2]))
    d.append(float(splits[3]))
    d.append(float(splits[4]))
    d.append(float(splits[5]))
    d.append(float(splits[6]))
    d.append(float(splits[7]))
    Data[int(splits[0])]=np.array(d)
file.close()

In [69]:
file = open("sDBN/part-r-00000",'r')
Data_sDBN = {}
for l in file.readlines():
    d=[]
    splits=l.split('\t')
    d.append(float(splits[1]))
    d.append(float(splits[2]))
    d.append(float(splits[3]))
    Data_sDBN[int(splits[0])]=np.array(d)
file.close()

In [16]:
Data_PBM = {}
for i in range(11):
    file = open("Docs/real_PBM/part-r-000"+str(i).zfill(2),'r')
    for l in file.readlines():
        d=[]
        splits=l.split('\t')
        d.append(float(splits[1]))
        d.append(float(splits[2]))
        d.append(float(splits[3]))
        d.append(float(splits[4]))
        d.append(float(splits[5]))
        d.append(float(splits[6]))
        d.append(float(splits[7]))
        d.append(float(splits[8]))
        d.append(float(splits[9]))
        d.append(float(splits[10]))
        d.append(float(splits[11]))
        d.append(float(splits[12]))
        d.append(float(splits[13]))
        d.append(float(splits[14]))
        d.append(float(splits[15]))
        d.append(float(splits[16]))
        Data_PBM[int(splits[0])]=np.array(d)
    file.close()

In [159]:
VALentine={}#В ПОСЛЕДНИЙ ДЕНЬ ИЗ-ЗА ЗАГРУЖЕННОСТИ ХАДУПА ПОПРОСИЛ НЕКОТОРЫЕ СЫРЫЕ ДАННЫЕ У ВАЛЕНТИНА. их перевел сам в статистики
file = open('features_9.txt')
for line in file.readlines():
    line = line.strip().split("\t");
    x=[]
    if int(line[2])<=0:
        continue
    x.append(int(line[2]))
    x.append(int(line[3]))
    x.append(int(line[4]))
    x.append(int(line[4])/x[0])
    x.append(float(line[5]))
    x.append(int(line[8]))
    x.append(int(line[9]))
    click_pos=line[6].strip().split()
    pos_click = line[7].strip().split()
    x.append(int(click_pos[0]))
    x.append(int(pos_click[0]))
    x.append(int(click_pos[0])/x[0])
    x.append(int(click_pos[0])/x[1])
    x.append(int(pos_click[0])/x[0])
    x.append(int(pos_click[0])/x[1])
    mean_pos_click = 0
    mean_click_pos = 0
    for cl in click_pos:
        mean_pos_click+=int(cl)
    x.append(mean_pos_click*1./len(click_pos))
    for lc in pos_click:
        mean_click_pos+=int(lc)
    x.append(mean_click_pos*1./len(pos_click))
    VALentine[int(line[0])]=x

In [13]:
file = open("Train_data.txt", 'w')
for i in train:
    try:
        x_pbm=Data_PBM[str(i[0])+"|"+str(i[1])]
        if i[1] not in Data.keys():
            x=np.zeros(7)
        else:
            x=Data[str(i[0])+"|"+str(i[1])]
        if i[1] not in Data_sDBN.keys():
            x_sDBN=np.zeros(3)
        else:
            x_sDBN=Data_sDBN[str(i[0])+"|"+str(i[1])]
        file.write(str(i[0])+'\t'+str(i[2])+'\t'+str(i[1])+'\t')
        for j in x:
            file.write(str(j)+'\t')
        for j in x_pbm:
            file.write(str(j)+'\t')
        for j in x_sDBN:
            file.write(str(j)+'\t')
        file.write('\n')
    except Exception:
        continue
file.close()

In [14]:
file = open("Test_data.txt", 'w')
for i in test:
    try:
        x_pbm=Data_PBM[str(i[0])+"|"+str(i[1])]
        if i[1] not in Data.keys():
            x=np.zeros(7)
        else:
            x=Data[str(i[0])+"|"+str(i[1])]
        if i[1] not in Data_sDBN.keys():
            x_sDBN=np.zeros(3)
        else:
            x_sDBN=Data_sDBN[str(i[0])+"|"+str(i[1])]
        file.write(str(i[0])+'\t'+str(-1)+'\t'+str(i[1])+'\t')
        for j in x:
            file.write(str(j)+'\t')
        for j in x_pbm:
            file.write(str(j)+'\t')
        for j in x_sDBN:
            file.write(str(j)+'\t')
        file.write('\n')
    except Exception:
        continue
file.close()

In [166]:
file = open("modelTest_data.txt", 'w')
for i in test:
    try:
        x_pbm=Data[i[1]]
        if i[1] not in Data_PBM.keys():
            x=np.zeros(16)
        else:
            x=Data_PBM[i[1]]
        if i[1] not in VALentine.keys():
            v=np.zeros(15)
        else:
            v=VALentine[i[1]]
        if str(i[0])+"|"+str(i[1]) not in Data_sDBN.keys():
            x_sDBN=np.zeros(3)
        else:
            x_sDBN=Data_sDBN[str(i[0])+"|"+str(i[1])]
        file.write(str(i[0])+'\t'+str(-1)+'\t'+str(i[1])+'\t')
        for j in x:
            file.write(str(j)+'\t')
        for j in x_pbm:
            file.write(str(j)+'\t')
        for j in x_sDBN:
            file.write(str(j)+'\t')
        for j in v:
            file.write(str(j)+'\t')
        file.write('\n')
    except Exception:
        continue
file.close()

In [167]:
file = open("modelTrain_data.txt", 'w')
for i in train:
    try:
        x_pbm=Data[i[1]]
        if i[1] not in Data_PBM.keys():
            x=np.zeros(16)
        else:
            x=Data_PBM[i[1]]
        if i[1] not in VALentine.keys():
            v=np.zeros(15)
        else:
            v=VALentine[i[1]]
        if str(i[0])+"|"+str(i[1]) not in Data_sDBN.keys():
            x_sDBN=np.zeros(3)
        else:
            x_sDBN=Data_sDBN[str(i[0])+"|"+str(i[1])]
        file.write(str(i[0])+'\t'+str(i[2])+'\t'+str(i[1])+'\t')
        for j in x:
            file.write(str(j)+'\t')
        for j in x_pbm:
            file.write(str(j)+'\t')
        for j in x_sDBN:
            file.write(str(j)+'\t')
        for j in v:
            file.write(str(j)+'\t')
        file.write('\n')
    except Exception:
        continue
file.close()

In [2]:
def load_data(filename):
    qid_data=[]
    y_data = []
    doc_ids=[]
    X_data=[]
    file = open(filename, 'r')
    for l in file.readlines():
        line=l.strip().split('\t')
        x=[]
        qid_data.append(int(line[0]))
        y_data.append(float(line[1]))
        doc_ids.append(int(line[2]))
        for i in range(3, len(line)):
            x.append(float(line[i]))
        X_data.append(x)
    qid_data=np.array(qid_data)
    y_data=np.array(y_data)
    X_data= np.array(X_data)
    doc_ids= np.array(doc_ids)
    group_data =np.unique(qid_data, return_counts=True)[1]
    return X_data, y_data, qid_data, group_data, doc_ids

In [3]:
X_train,y_train, qid_train, group_train, doc_ids_train = load_data("Train_data.txt")
X_test,y_test, qid_test, group_test, doc_ids_test = load_data("Test_data.txt")

In [4]:
X_train_new,y_train, qid_train, group_train, doc_ids_train = load_data("modelTrain_data.txt")
X_test_new,y_test, qid_test, group_test, doc_ids_test = load_data("modelTest_data.txt")

In [5]:
X_train = np.hstack((X_train,X_train_new))
X_test = np.hstack((X_test,X_test_new))

In [19]:
idx_train = np.where(X_train[:,0]==0.)
idx_test = np.where(X_test[:,0]==0.)
doc_ids_test_new = np.delete(doc_ids_test, idx_test[0],axis=0)
qid_train_new  = np.delete(qid_train, idx_train[0],axis=0)
qid_test_new = np.delete(qid_test, idx_test[0],axis=0)
group_train_new=np.unique(qid_train_new, return_counts=True)[1]
group_test_new=np.unique(qid_test_new, return_counts=True)[1]
y_train_new = np.delete(y_train, idx_train[0],axis=0)
X_train_new=np.delete(X_train, idx_train[0],axis=0)
X_test_new=np.delete(X_test, idx_test[0],axis=0)

In [13]:
X_test_new.shape

(149819, 71)

In [175]:
def train_val_split(X_data, y_data, qid_data, group_sizes, test_size=0.05):
    queries_test_size = int(group_sizes.shape[0] * test_size)
    queries_train_size = group_sizes.shape[0] - queries_test_size
    print(group_sizes.shape[0], queries_test_size, queries_train_size)

    group_train, group_val = group_sizes[:queries_train_size], group_sizes[queries_train_size:]
    print(group_train.shape[0], group_val.shape[0])

    train_x_len = group_train.sum()
    print(X_data.shape[0], train_x_len, X_data.shape[0] - train_x_len)

    X_train, X_val = X_data[:train_x_len], X_data[train_x_len:]
    y_train, y_val = y_data[:train_x_len], y_data[train_x_len:]
    qid_train, qid_val = qid_data[:train_x_len], qid_data[train_x_len:]

    return X_train, y_train, qid_train, group_train, X_val, y_val, qid_val, group_val

In [40]:
X_train, y_train, qid_train, group_train, X_val, y_val, qid_val, group_val = train_val_split(X_train, y_train, qid_train, group_train)

2111 422 1689
1689 422
95428 76141 19287


In [27]:
poly = PolynomialFeatures(2)
X_train_poly=poly.fit_transform(X_train_new)
X_test_poly=poly.fit_transform(X_test_new)

In [7]:
def dcg(y, k=5):
    k_=min(len(y),k)
    return np.sum([(np.power(2, y[i]) - 1) / (np.log2(i + 2) + 1) for i in range(k_)])
def ideal_dcg(scores):
    scores = [score for score in np.sort(scores, kind='mergesort')[::-1]]
    return dcg(scores)
def get_pairs(true_scores):
    len_of_scores = len(true_scores)
    for i in range(len_of_scores):
        for j in range(i, len_of_scores):
            if true_scores[i] > true_scores[j]:
                yield (i, j)

def delta_ndcg(i,j,idcg, y_true):
    i_pow = np.power(2, y_true[i]) - 1
    j_pow = np.power(2, y_true[j]) - 1
    i_log = np.log2(i + 2)
    j_log = np.log2(j + 2)
    return abs(i_pow / j_log - i_pow / i_log + j_pow / i_log - j_pow / j_log) / idcg

In [8]:
def lambdas_and_w(args):
    y_true, y_pred, qid = args
    sorted_indexes = np.argsort(y_pred, kind='mergesort')[::-1]
    rev_indexes = np.argsort(sorted_indexes)
    #print(sorted_indexes, rev_indexes)
    y_true = y_true[sorted_indexes]
    y_pred = y_pred[sorted_indexes]
    dcg_real=ideal_dcg(y_true)
    lambdas=np.zeros(len(y_true))
    w=np.zeros(len(y_true))
    for i, j in get_pairs(y_true):
        d_ndcg=delta_ndcg(i,j,dcg_real, y_true)
        #print(i,j,d_ndcg)
        diff=min(abs(y_pred[i]-y_pred[j]),20)
        sig=expit(-diff)
        lambda_val = -d_ndcg * sig
        w_val = sig * (1 - sig) * d_ndcg
        #print(i,j,d_ndcg,diff,sig, lambda_val, w_val)
        lambdas[i] += lambda_val
        lambdas[j] -= lambda_val
        w[i] += w_val
        w[j] += w_val
    #print(lambdas,w)
    return lambdas[rev_indexes], w[rev_indexes], qid

In [9]:
def gradient(pred, dtrain):
    Y = np.array(dtrain.get_label())
    pred=np.array(pred)
    qids=np.unique(qid_train_new)
    true_scores = [Y[np.where(qid_train_new==qid)] for qid in qids]
    pred_scores=[pred[np.where(qid_train_new==qid)] for qid in qids]
    grad = np.zeros(Y.shape)
    hess = np.zeros(Y.shape)
    pool = Pool(6)
    for lambda_val, w_val, qid in pool.map(lambdas_and_w,
                                             zip(true_scores, pred_scores, qids),
                                             chunksize=1):
        grad[np.where(qid_train_new==qid)] = lambda_val
        hess[np.where(qid_train_new==qid)] = w_val
#     for true,pred,qid in zip(true_scores, pred_scores, qids):
#         lambda_val, w_val=lambdas_and_w(y_true=true,y_pred=pred)
#         grad[np.where(qid_train==qid)] = lambda_val
#         hess[np.where(qid_train==qid)] = w_val
    return grad, hess

In [10]:
dtrain = xgb.DMatrix(data = X_train_new, label = y_train_new)
dtrain.set_group(group_train_new)
#dval = xgb.DMatrix(data = X_val, label = y_val)
#dval.set_group(group_val)
dtest = xgb.DMatrix(data = X_test_new)
dtest.set_group(group_test_new)

In [11]:
from multiprocessing import Pool
params = {'eta': 0.3,  'max_depth': 7, 'eval_metric': 'ndcg@5','subsample': 0.7, 'num_parallel_tree': 6}#, 'tree_method': 'gpu_hist'}
xgb_model = xgb.train(params, dtrain, num_boost_round=50, evals=[(dtrain, 'validate')],
                        obj=gradient,# xgb_model="my_xgboost_new_version_1.2_12_100.xgb",
                        verbose_eval=True)

[0]	validate-ndcg@5:0.70072
[1]	validate-ndcg@5:0.70068
[2]	validate-ndcg@5:0.69901


Process ForkPoolWorker-3:
Process ForkPoolWorker-1:
Process ForkPoolWorker-2:
Process ForkPoolWorker-4:
Process ForkPoolWorker-5:
Process ForkPoolWorker-8:
Process ForkPoolWorker-10:
Process ForkPoolWorker-7:
Process ForkPoolWorker-12:
Process ForkPoolWorker-13:
Process ForkPoolWorker-14:
Process ForkPoolWorker-16:
Process ForkPoolWorker-17:
Process ForkPoolWorker-18:
Process ForkPoolWorker-6:
Process ForkPoolWorker-20:
Process ForkPoolWorker-9:
Process ForkPoolWorker-21:
Process ForkPoolWorker-11:
Process ForkPoolWorker-15:
Process ForkPoolWorker-19:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent

  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 9

  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
KeyboardInterrupt
KeyboardInterrupt
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/connection.py", line 216, in recv_bytes
    buf = self._recv_bytes(maxlength)
KeyboardInterrupt
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/connection.py", line 379, in _recv
    chunk = read(handle, remaining)
KeyboardInterrupt
KeyboardInterrupt
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/connection.py", line 379, in _recv
    chunk = read(handle, remaining)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/connection.py", line 379, in _recv
    chunk = read(handle, remaining)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/connection.py", line 407, in _recv_bytes
    buf = self._recv(4)
KeyboardInterrupt

KeyboardInterrupt: 

Process ForkPoolWorker-24:
Process ForkPoolWorker-26:
Process ForkPoolWorker-27:
Process ForkPoolWorker-28:
Process ForkPoolWorker-25:
Process ForkPoolWorker-30:
Process ForkPoolWorker-29:
Process ForkPoolWorker-31:
Process ForkPoolWorker-34:
Process ForkPoolWorker-38:
Process ForkPoolWorker-36:
Process ForkPoolWorker-37:
Process ForkPoolWorker-39:
Process ForkPoolWorker-41:
Process ForkPoolWorker-22:
Process ForkPoolWorker-35:
Process ForkPoolWorker-33:
Process ForkPoolWorker-32:
Process ForkPoolWorker-40:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last

  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/pytho

In [58]:
pred = xgb_model.predict(dtest)

In [57]:
xgb_model.best_iteration

49

In [25]:
print(qid_test_new.shape, doc_ids_test_new.shape)

(190097,) (190097,)


In [189]:
xgb_model.save_model("my_xgboost_new_version_1.2_12_100.xgb")

In [20]:
def save_submission(pred_qids, preds, all_doc_ids, filename):
    fout = open(filename, 'w')
    fout.write('QueryId,DocumentId\n')
    for qid in np.unique(pred_qids):
        q_doc_idxs = np.argwhere(pred_qids == qid).ravel()
        doc_ids = copy.deepcopy(all_doc_ids[q_doc_idxs])
        q_doc_scores = preds[q_doc_idxs]
        sorted_doc_ids = doc_ids[np.argsort(q_doc_scores)[::-1]]
        for did in sorted_doc_ids:
            fout.write('{0},{1}\n'.format(qid, did))
        
    fout.close

In [59]:
save_submission(qid_test_new,pred,doc_ids_test_new, 'vot_eto_prikol2.txt')

# Analysis/Modeling
Do work here

In [21]:
from catboost import CatBoost, Pool
InteractiveShell.ast_node_interactivity = 'last'
train = Pool(
    data=X_train_new,
    label=y_train_new,
    group_id=qid_train_new
)
test = Pool(data=X_test_new, group_id=qid_test_new)
default_parameters = {
    'iterations': 800,
    'custom_metric': ['NDCG:top=5'],
    'verbose': False,
    'subsample': 0.6,
    'eta': 0.35,
    'depth': 5
}
parameters = deepcopy(default_parameters)
parameters['loss_function'] = 'YetiRankPairwise'
parameters['train_dir'] = 'YetiRankPairwise'
model_catboost = CatBoost(parameters)

In [23]:
model_catboost.fit(train, eval_set=train, plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [24]:
pred_catboost = model_catboost.predict(test)
save_submission(qid_test_new,pred_catboost,doc_ids_test_new, 'made_by_korova-virus.txt')

# Попытки сглаживания

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer
import requests
import re
from stop_words import get_stop_words
from rank_bm25 import BM25Okapi
from tqdm import tqdm

In [10]:
import pymorphy2
morph = pymorphy2.MorphAnalyzer()

In [60]:
def api_similarity(m, w1, w2):
    url = '/'.join(['https://rusvectores.org', m, w1 + '__' + w2, 'api', 'similarity/'])
    r = requests.get(url, stream=True)
    return r.text.split('\t')[0]

In [79]:
MODEL = 'ruscorpora_upos_cbow_300_20_2019'
api_similarity(MODEL, 'лис', 'стул')

'0.06208226457238197'

In [109]:
def query(filename, flag=True):
    file = open(filename, 'r')
    for line in file.readlines():
        l= line.strip().split('\t')
        if(flag):
            yield morph.normal_forms(l[1].strip())[0]
        else:
            yield morph.normal_forms(l[0].strip())[0]
    file.close()

In [110]:
vectorizer = TfidfVectorizer(stop_words=stop_words)

In [111]:
q0 = set(train[:,0])

TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
                dtype=<class 'numpy.float64'>, encoding='utf-8',
                input='content', lowercase=True, max_df=1.0, max_features=None,
                min_df=1, ngram_range=(1, 1), norm='l2', preprocessor=None,
                smooth_idf=True,
                stop_words=['a', 'about', 'above', 'after', 'again', 'against',
                            'all', 'am', 'an', 'and', 'any', 'are', "aren't",
                            'as', 'at', 'be', 'because', 'been', 'before',
                            'being', 'below', 'between', 'both', 'but', 'by',
                            "can't", 'cannot', 'could', "couldn't", 'did', ...],
                strip_accents=None, sublinear_tf=False,
                token_pattern='(?u)\\b\\w\\w+\\b', tokenizer=None, use_idf=True,
                vocabulary=None)

In [10]:
q_train = np.unique(train[:,0])
q_train

array([   2,   14,   15, ..., 6293, 6297, 6305])

In [24]:
q2=train[np.where(train[:,0]==2)][:,1]
q2
a={"hgfhj":454}

In [26]:
a["hhjj"]=545
a

{'hgfhj': 454, 'hhjj': 545}

In [27]:
DQ={}
for i in range(11):
    print(i)
    file = open("QDocs/PBM/part-r-000"+str(i).zfill(2), 'r')
    for line in file.readlines():
        l= line.strip().split('\t')
        ind = int(l[1])
        if ind not in q2:
            continue
        #if ind in train[:,1]:
        if ind in DQ.keys():
            x=np.zeros(len(l)-2)
            for i in range(2,len(l)):
                x[i-2]=np.float16(l[i])
            DQ[ind][l[0].strip()]=x
        else:
            x=np.zeros(len(l)-2)
            for i in range(2,len(l)):
                x[i-2]=np.float16(l[i])
            DQ[ind]={l[0].strip():x}
    file.close()

0
1
2
3
4
5
6
7
8
9
10


In [12]:
DQ

{136185: [{'аня балакина северск томской': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'https ok ru как называется животноводческий комплекс в калужской области открытой женой дмитрия медведева премьер министра светланой медведевой': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'генадий артемьев борисоглебск занимается ли он благотворительностью': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'посёлок товарково калужской области br 2 как добраться от москвы': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'гку ко инновационный культурный центр борисенков дмитрий викторович': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'говно течёт по балабанову а миллиарды из казны с калуга водоканал текут фашисту губернатору артамонову': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])},
  {'дтп 31 01 17 в барятинском районе калужской области': a

In [11]:
def semantical(w1, w2):
    N=0
    S=0.
    for i in w1.split(): 
        l=0.
        n=0
        for j in w2.split():
            try:
                s=model.similarity( i, j)
            except:
                continue
            l+=float(s)
            n+=1
        if(n==0):
            continue
        S+=l/n
        N+=1
    if(N==0):
        return 0
    return S/N

def lexical(q, Dq):
    tokenized_corpus = [doc.split(" ") for doc in Dq]
    bm25 = BM25Okapi(tokenized_corpus)
    tokenized_query = q.split(" ")
    x=bm25.get_scores(tokenized_query)
    if x.sum()!=0:
        return x/x.sum()
    else:
        return x

def score(i):
    if i[1] in DQ.keys():
        coefs=np.zeros(len(DQ[i[1]]))
        lex = lexical(QUERY[i[0]], DQ[i[1]])
        for j,query in enumerate(DQ[i[1]]):
            coefs[j]=1.0*lex[j]#+0.5*semantical(QUERY[i[0]], query)
        QQ[str(i[0])+"_"+str(i[1])]=coefs
        #return i[0],i[1], coefs
    #return None, None, None

In [8]:
QQ={}
from multiprocessing import Pool
pool=Pool(6)
file = open("match.txt", 'w')
for q_id, doc_id, coefs in pool.map(score,train, chunksize=1):
    if q_id is not None:
        s=str(q_id)+'\t'+str(doc_id)+'\t'
        for i in range(len(coefs)):
            s+=QD[doc_id][i]+':'+str(coef[i])+'\t'
        file.writeline(s)

Process ForkPoolWorker-2:
Traceback (most recent call last):
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 121, in worker
    result = (True, func(*args, **kwds))
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 44, in mapstar
    return list(map(*args))
  File "<ipython-input-6-34d185fcd892>", line 35, in score
    lex = lexical(QUERY[i[0]], DQ[i[1]])
  File "<ipython-input-6-34d185fcd892>", line 26, in lexical
    x=bm25.get_scores(tokenized_query)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/site-packages/rank_bm25.py", line 112, in get_scores
    q_freq = np.array([(doc.get(q) or 0) 

Traceback (most recent call last):
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3331, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-8-c0af1e9d3da0>", line 5, in <module>
    for q_id, doc_id, coefs in pool.map(score,train, chunksize=1):
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 268, in map
    return self._map_async(func, iterable, mapstar, chunksize).get()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 651, in get
    self.wait(timeout)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 648, in wait
    self._event.wait(timeout)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/threading.py", line 552, in wait
    signaled = self._cond.wait(timeout)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python

Exception in thread Thread-4:
Traceback (most recent call last):
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/threading.py", line 926, in _bootstrap_inner
    self.run()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 412, in _handle_workers
    pool._maintain_pool()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 248, in _maintain_pool
    self._repopulate_pool()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 241, in _repopulate_pool
    w.start()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 112, in start
    self._popen = self._Popen(self)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/context.p

KeyboardInterrupt: 

Process ForkPoolWorker-6:
Traceback (most recent call last):
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 121, in worker
    result = (True, func(*args, **kwds))
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/multiprocessing/pool.py", line 44, in mapstar
    return list(map(*args))
  File "<ipython-input-6-34d185fcd892>", line 35, in score
    lex = lexical(QUERY[i[0]], DQ[i[1]])
  File "<ipython-input-6-34d185fcd892>", line 24, in lexical
    bm25 = BM25Okapi(tokenized_corpus)
  File "/home/demontego/anaconda3/envs/sphere-py37/lib/python3.7/site-packages/rank_bm25.py", line 77, in __init__
    super().__init__(corpus, tokenizer)
  Fi

In [12]:
QQ={}
for i in tqdm(train):
    if i[1] in DQ.keys():
        coefs=np.zeros(len(DQ[i[1]]))
        lex = lexical(QUERY[i[0]], DQ[i[1]])
        for j,query in enumerate(DQ[i[1]]):
            coefs[j]=0.5*lex[j]+0.5*semantical(QUERY[i[0]], query)
        QQ[str(i[0])+"_"+str(i[1])]=coefs


  2%|▏         | 3694/202079 [04:37<18:32:04,  2.97it/s]


  3%|▎         | 6311/202079 [19:11<14:28:57,  3.75it/s]


  5%|▌         | 10400/202079 [27:25<59:40, 53.54it/s]  


  6%|▌         | 12226/202079 [30:14<9:36:30,  5.49it/s] 


  8%|▊         | 15801/202079 [38:07<12:45:28,  4.06it/s]


...

 92%|█████████▏| 186538/202079 [4:17:16<45:40,  5.67it/s]


 94%|█████████▍| 190735/202079 [4:22:42<24:21,  7.76it/s]


 96%|█████████▌| 194489/202079 [4:25:22<01:03, 119.56it/s]


 98%|█████████▊| 198769/202079 [4:28:29<01:39, 33.17it/s]


100%|██████████| 202079/202079 [4:32:01<00:00, 12.38it/s]


In [14]:
for i in tqdm(test):
    if i[1] in DQ.keys():
        coefs=np.zeros(len(DQ[i[1]]))
        lex = lexical(QUERY[i[0]], DQ[i[1]])
        for j,query in enumerate(DQ[i[1]]):
            coefs[j]=0.5*lex[j]+0.5*semantical(QUERY[i[0]], query)
        QQ[str(i[0])+"_"+str(i[1])]=coefs


  1%|          | 4998/403971 [06:33<58:29, 113.69it/s]


  2%|▏         | 9696/403971 [14:14<22:12:58,  4.93it/s]


  4%|▎         | 14931/403971 [17:09<7:49:38, 13.81it/s] 


  5%|▍         | 19500/403971 [24:43<6:25:10, 16.64it/s]


  6%|▌         | 24538/403971 [28:42<7:59:27, 13.19it/s]


...

 97%|█████████▋| 390079/403971 [8:09:30<13:06, 17.67it/s]


 98%|█████████▊| 393926/403971 [8:12:10<10:15, 16.33it/s]


 98%|█████████▊| 397318/403971 [8:14:53<02:06, 52.43it/s]


 99%|█████████▉| 401671/403971 [8:19:15<20:05,  1.91it/s]


100%|██████████| 403971/403971 [8:20:22<00:00, 13.46it/s]


In [10]:
import wget
import zipfile
import sys
import gensim, logging
model_url = 'http://vectors.nlpl.eu/repository/20/65.zip'
#m = wget.download(model_url)
model_file = model_url.split('/')[-1]
with zipfile.ZipFile(model_file, 'r') as archive:
    stream = archive.open('model.bin')
    model = gensim.models.KeyedVectors.load_word2vec_format(stream, binary=True)

 28%|██▊       | 55606/202079 [08:57<1:52:16, 21.74it/s]

In [27]:
file= open('matching_q.txt', 'w')
for i in QQ.keys():
    clear_output()
    split=i.split("_")
    print(split[0])
    doc_id= int(split[1])
    s=split[0]+'\t'+split[1]
    queries = DQ[doc_id]
    scores = QQ[i]
    for j in range(len(queries)):
        s+="\t"+queries[j]+":"+str(scores[j])
    s+='\n'
    file.write(s)
file.close()

6310


In [37]:
file = open("new_data.txt",  'w')
for i in range(6):
    file_match = open("check/QQ/part-r-000"+str(i).zfill(2), 'r')
    for line in file_match.readlines():
        split=line.split("\t")
        if (int(split[0])!=i):
            continue
        vectors=DQ[int(split[1])]
        res=np.zeros(15)
        for i in range(2, len(split)):
            q=split[i].split(":")[0]
            coef=float(split[i].split(":")[1])
            #print(coef, vectors[q], vectors[q]*coef)
            res+=vectors[q]*coef
        result=split[0]+'\t'+split[1]
        for i in res:
            result+='\t'+str(i)
        result+='\n'
        file.write(result)
    file_match.close()
file.close()

0
1
2
3
4
5


In [9]:
def new_data(query_id):
    seq = s[query_id]
    DQ = {}
    for i in range(11):
        file = open("QDocs/PBM/part-r-000"+str(i).zfill(2), 'r')
        for line in file.readlines():
            l = line.strip().split('\t')
            ind = int(l[1])
            if ind not in seq:
                continue
            # if ind in train[:,1]:
            if ind in DQ.keys():
                x = np.zeros(len(l)-2)
                for i in range(2, len(l)):
                    x[i-2] = np.float16(l[i])
                DQ[ind][l[0].strip()] = x
            else:
                x = np.zeros(len(l)-2)
                for i in range(2, len(l)):
                    x[i-2] = np.float16(l[i])
                DQ[ind] = {l[0].strip(): x}
    file.close()
    #file = open("new_data.txt",  'w')
    file = open("new_data_"+str(current_process().pid % 6)+".txt",  'a')
    for i in range(6):
        file_match = open("check/QQ/part-r-000"+str(i).zfill(2), 'r')
        for line in file_match.readlines():
            split = line.split("\t")
            if (int(split[0]) != query_id):
                continue
            vectors = DQ[int(split[1])]
            res = np.zeros(15)
            for i in range(2, len(split)):
                q = split[i].split(":")[0]
                coef = float(split[i].split(":")[1])
                #print(coef, vectors[q], vectors[q]*coef)
                res += vectors[q]*coef
            result = split[0]+'\t'+split[1]
            for i in res:
                result += '\t'+str(i)
            result += '\n'
            file.write(result)
        file_match.close()
    file.close()